In [1]:
import logging
import random
from tqdm import tqdm
import os
import asyncio
from dotenv import load_dotenv

if "dir_changed" not in locals():
    os.chdir("..")
    loaded = load_dotenv(override=True)
    dir_changed = True

Using log_level=INFO


{"message": "PyTorch version 2.3.1 available.", "timestamp": "2024-08-20T08:20:00.596856Z", "severity": "INFO", "labels": {"view": "query-processing", "searchId": ""}}


In [ ]:
from prompt_optimization.operators.mutation import Mutation
from prompt_optimization.utils.data import load_summeval_jsonl
from prompt_optimization.prompt_eval.exact_match_evaluator import (
    ExactMatchEvaluatorConfig,
    ExactMatchEvaluator,
)
from prompt_optimization.utils.prompt import prompt_set_union

from prompt_optimization.types.prompt import Prompt
from prompt_optimization.utils.data import (
    load_rewardbench_references,
    CHAT_SUBSETS,
    CHAT_HARD_SUBSETS,
    SAFETY_SUBSETS,
    REASONING_SUBSETS,
)
from prompt_optimization.prompt_eval.dict_similarity_evaluator2 import (
    DictSimilarityEvaluator2,
    DictSimilarityEvaluator2Config,
)
from prompt_optimization.llm.open_ai_compliant_llm_engine import (
    OpenAICompliantLLMEngine,
)

In [2]:
references = load_summeval_jsonl("data/summeval.jsonl")

random.seed(123)
references_shuffled = random.sample(references, len(references))

se_train = references_shuffled[:25]
se_test = references_shuffled[50:150]

In [3]:
training_examples_per_subset = 1
validations_per_subset = 8

subsets_map = {
    "chat": CHAT_SUBSETS,
    "chat_hard": CHAT_HARD_SUBSETS,
    "safety": SAFETY_SUBSETS,
    "reasoning": REASONING_SUBSETS,
}

subsets_all = [subset for subsets in subsets_map.values() for subset in subsets]

subset_data = {subset: load_rewardbench_references([subset]) for subset in subsets_all}

rb_train = []
for subset in subsets_all:
    rb_train.extend(subset_data[subset][:training_examples_per_subset])

rb_test = []
for category, subsets in subsets_map.items():
    for subset in subsets:
        rb_test.extend(
            subset_data[subset][
                training_examples_per_subset : training_examples_per_subset
                + validations_per_subset
            ]
        )

# shuffle rb_train
random.seed(123)
rb_train = random.sample(rb_train, len(rb_train))

In [4]:
api_keys = [
    os.environ["DEEPINFRA_API_KEY_A1"],
    os.environ["DEEPINFRA_API_KEY_A2"],
    os.environ["DEEPINFRA_API_KEY_A3"],
    os.environ["DEEPINFRA_API_KEY_A4"],
]
llama31_70b = OpenAICompliantLLMEngine(
    base_url=os.environ["DEEPINFRA_BASE_URL"],
    api_keys=api_keys,
    model="meta-llama/Meta-Llama-3.1-70B-Instruct",
)
llama31_70b_eval = OpenAICompliantLLMEngine(
    base_url=os.environ["DEEPINFRA_BASE_URL"],
    api_keys=api_keys,
    model="meta-llama/Meta-Llama-3.1-70B-Instruct",
    temperature=0.0,
)
llama31_70b_b = OpenAICompliantLLMEngine(
    base_url=os.environ["DEEPINFRA_BASE_URL"],
    api_keys=api_keys,
    model="meta-llama/Meta-Llama-3.1-70B-Instruct",
)
llama31_70b_eval_b = OpenAICompliantLLMEngine(
    base_url=os.environ["DEEPINFRA_BASE_URL"],
    api_keys=api_keys,
    model="meta-llama/Meta-Llama-3.1-70B-Instruct",
    temperature=0.0,
)

In [5]:
meta_prompt = """{rnd}
Generate a variation of the following prompt:

<PROMPT>
{prompt}
</PROMPT>

The generated prompt should be contain all information and instructions of the original prompt, but worded in a different way.
Important: change as much about the prompt as possible, while keeping the meaning and instructions the same.

Provide the new instruction inside <INSTR> tags like this:
<INSTR>...</INSTR>
"""

se_system = """You are an expert system at evaluating created summaries on the dimensions of coherence, consistency, fluency, and relevance."""

se_instructions = """
You will evaluate the quality of a given summary, with respect to a reference on four dimensions.

Output your evaluation as a JSON object like this:
{
    "coherence: <float between 1 and 5>",
    "consistency: <float between 1 and 5>",
    "fluency: <float between 1 and 5>",
    "relevance: <float between 1 and 5>"
}

Before you output the JSON dict, lay out your reasoning step by step.
"""

rb_system = "You are a fair judge assistant tasked with providing clear, objective feedback based on specific criteria, ensuring each assessment reflects the absolute standards set for performance."

rb_prompt_v2 = (
    "Please act as an impartial judge and evaluate the quality of the responses provided by two AI assistants to the user question displayed below. "
    "You should choose the assistant that follows the user's instructions and answers the user's question better. Your evaluation should consider "
    "factors such as the helpfulness, relevance, accuracy, depth, creativity, and level of detail of their responses. Begin your evaluation by "
    "comparing the two responses and provide a short explanation. Avoid any position biases and ensure that the order in which the responses were "
    "presented does not influence your decision. Do not allow the length of the responses to influence your evaluation. Do not favor certain names "
    "of the assistants. Be as objective as possible. After providing your explanation, output your final verdict by strictly following this format: "
    '"[[A]]" if assistant A is better, "[[B]]" if assistant B is better.'  # removed tie option as , and \"[[C]]\ " for a tie
)

In [6]:
prompt_set_se = [Prompt(prompt=se_instructions)]

prompt_set_rb = [Prompt(prompt=rb_prompt_v2)]

In [7]:
logger = logging.getLogger()
# logger.setLevel(logging.WARNING)

### Trainset evaluators

In [8]:
k = 5

conf = DictSimilarityEvaluator2Config(
    testset=se_train[:k],
    llm=llama31_70b_eval,
    validation=False,
    system_prompt=se_system,
    instruction_execution_prompt="{input}\n\n{instruction}",
)
se_metric = DictSimilarityEvaluator2(conf)

conf = ExactMatchEvaluatorConfig(
    testset=rb_train[:k],
    llm=llama31_70b_eval_b,
    validation=False,
    output_extraction_regex=r"\[\[.*\]\]",
    system_prompt=rb_system,
    instruction_execution_prompt="{instruction}\n\n{input}",
)
rb_metric = ExactMatchEvaluator(conf)

conf = DictSimilarityEvaluator2Config(
    testset=se_test,
    llm=llama31_70b_eval_b,
    validation=True,
    system_prompt=se_system,
    instruction_execution_prompt="{input}\n\n{instruction}",
)
se_val = DictSimilarityEvaluator2(conf)

conf = ExactMatchEvaluatorConfig(
    testset=rb_test,
    llm=llama31_70b_eval_b,
    validation=True,
    output_extraction_regex=r"\[\[.*\]\]",
    system_prompt=rb_system,
    instruction_execution_prompt="{instruction}\n\n{input}",
)
rb_val = ExactMatchEvaluator(conf)

### Optimizer

In [9]:
def best_non_val(prompt_set):
    return sorted(
        [p for p in prompt_set if p.mean_validation_score is None],
        key=lambda p: p.mean_score,
        reverse=True,
    )[0]

In [10]:
n = 20
val_steps = [5, 10]

mutator_se = Mutation(llama31_70b, meta_prompt=meta_prompt)
mutator_rb = Mutation(llama31_70b_b, meta_prompt=meta_prompt)

validation_tasks = []
for step in tqdm(range(n)):
    # trainset eval
    await asyncio.gather(se_metric(prompt_set_se), rb_metric(prompt_set_rb))

    # mutation
    best_se = sorted(prompt_set_se, key=lambda x: x.mean_score, reverse=True)[0]
    best_rb = sorted(prompt_set_rb, key=lambda x: x.mean_score, reverse=True)[0]

    # validation
    if step in val_steps:
        await asyncio.gather(
            se_val([best_non_val(prompt_set_se)]), rb_val([best_non_val(prompt_set_rb)])
        )

    new_prompts = await asyncio.gather(mutator_se([best_se]), mutator_rb([best_rb]))

    prompt_set_se = prompt_set_union(prompt_set_se, new_prompts[0])
    prompt_set_rb = prompt_set_union(prompt_set_rb, new_prompts[1])

await asyncio.gather(se_metric(prompt_set_se), rb_metric(prompt_set_rb))

await asyncio.gather(
    se_val([best_non_val(prompt_set_se)]), rb_val([best_non_val(prompt_set_rb)])
)

  0%|          | 0/20 [00:00<?, ?it/s]{"message": "Cache hit from key: {\"base_url\": \"https://api.deepinfra.com/v1/openai/\", \"max_tokens\": 4096, \"messages\": [{\"content\": \"Y...", "timestamp": "2024-08-20T08:20:28.189893Z", "severity": "INFO", "labels": {"view": "query-processing", "searchId": ""}}
{"message": "Prompt: \\nYou will evaluate the quality of a given summary, with respect to a reference on four dimensions.\\n\\nOutput your evaluation as a JSON obje [...] the JSON dict, lay out your reasoning step by step.\\n\nReference: {\"coherence\": 4.0, \"consistency\": 5.0, \"fluency\": 5.0, \"relevance\": 4.0}\nActual: ['To evaluate the quality of the given summary, I will assess it on four dimensions: coherence, consistency, fluency, and relevance. Here\\'s [...]  based on my analysis of the summary and reference.']", "timestamp": "2024-08-20T08:20:28.190997Z", "severity": "INFO", "labels": {"view": "query-processing", "searchId": ""}}
{"message": "Evaluated 1/5 queries.", "t

[[Prompt(prompt='Assess the effectiveness of a provided summary in relation to a given  [...] een 1 and 5, inclusive.' (len=648), mean_score=0.4434, mean_validation_score=0.4478, zero_score_cases=False)],
 [Prompt(prompt='Assume the role of a neutral arbiter and assess the merits of the resp [...] t B is deemed superior.' (len=1032), mean_score=0.8000, mean_validation_score=0.6932, zero_score_cases=True)]]

In [11]:
prompt_set_se

[Prompt(prompt='\nYou will evaluate the quality of a given summary, with respect to a  [...] asoning step by step.\n' (len=393), mean_score=0.4482, mean_validation_score=0.4819, zero_score_cases=False),
 Prompt(prompt='Your task is to assess the effectiveness of a summary in relation to a [...] cified range of 1 to 5.' (len=757), mean_score=0.4256, mean_validation_score=None, zero_score_cases=False),
 Prompt(prompt='Assess the quality of a provided summary in relation to a reference te [...] d on a scale of 1 to 5.' (len=588), mean_score=0.3926, mean_validation_score=None, zero_score_cases=False),
 Prompt(prompt='Assess the quality of a provided summary in relation to a given refere [...] ecedes the JSON output.' (len=612), mean_score=0.4360, mean_validation_score=None, zero_score_cases=False),
 Prompt(prompt='Assess the summary provided by evaluating its alignment with the refer [...] ation to the reference.' (len=680), mean_score=0.3287, mean_validation_score=None, zero_score_cases=F

In [12]:
prompt_set_rb

[Prompt(prompt='Please act as an impartial judge and evaluate the quality of the respo [...]  assistant B is better.' (len=915), mean_score=0.8000, mean_validation_score=0.7386, zero_score_cases=True),
 Prompt(prompt='Assume the role of a neutral arbiter and conduct a thorough assessment [...] t B is deemed superior.' (len=1064), mean_score=0.2000, mean_validation_score=None, zero_score_cases=True),
 Prompt(prompt='Assume the role of a neutral arbiter and conduct a thorough assessment [...] t B is deemed superior.' (len=1110), mean_score=0.4000, mean_validation_score=None, zero_score_cases=True),
 Prompt(prompt='Assume the role of a neutral arbiter and conduct a thorough assessment [...] t B is deemed superior.' (len=1105), mean_score=0.2000, mean_validation_score=None, zero_score_cases=True),
 Prompt(prompt='Assume the role of a neutral arbiter and conduct a thorough assessment [...] t B is deemed superior.' (len=1080), mean_score=0.6000, mean_validation_score=0.5795, zero_score_cases

In [13]:
import numpy as np
from prompt_optimization.utils.prompt import add_embedding_space_representations

await add_embedding_space_representations(
    prompt_set_se, os.environ["PERSONAL_OPENAI_KEY"]
)
await add_embedding_space_representations(
    prompt_set_rb, os.environ["PERSONAL_OPENAI_KEY"]
)

embeddings_se = np.array([p.embedding for p in prompt_set_se])
embeddings_rb = np.array([p.embedding for p in prompt_set_rb])


def average_pairwise_cosine_similarity(embeddings):
    # Normalize the vectors
    normalized_embeddings = embeddings / np.linalg.norm(
        embeddings, axis=1, keepdims=True
    )

    # Compute the dot product
    similarity_matrix = np.dot(normalized_embeddings, normalized_embeddings.T)

    # Get the upper triangle of the similarity matrix
    upper_tri = np.triu(similarity_matrix, k=1)

    # Calculate the average
    n = embeddings.shape[0]
    average_similarity = np.sum(upper_tri) / (n * (n - 1) / 2)

    return average_similarity


(
    average_pairwise_cosine_similarity(embeddings_se),
    average_pairwise_cosine_similarity(embeddings_rb),
)

(0.9017424102328611, 0.9787543346624815)

In [14]:
from Levenshtein import distance


def average_pairwise_levenshtein_distance(strings):
    """Compute the average pairwise Levenshtein distance for a list of strings."""
    if not strings:
        return 0

    n = len(strings)
    total_distance = 0
    pair_count = 0

    for i in range(n):
        for j in range(i + 1, n):
            total_distance += distance(strings[i], strings[j])
            pair_count += 1

    if pair_count == 0:
        return 0

    return total_distance / pair_count


(
    average_pairwise_levenshtein_distance([p.prompt for p in prompt_set_se]),
    average_pairwise_levenshtein_distance([p.prompt for p in prompt_set_rb]),
)

(358.6190476190476, 247.97619047619048)

In [15]:
await se_val(prompt_set_se)

{"message": "Cache hit from key: {\"base_url\": \"https://api.deepinfra.com/v1/openai/\", \"max_tokens\": 4096, \"messages\": [{\"content\": \"Y...", "timestamp": "2024-08-20T08:20:32.698984Z", "severity": "INFO", "labels": {"view": "query-processing", "searchId": ""}}
{"message": "Prompt: \\nYou will evaluate the quality of a given summary, with respect to a reference on four dimensions.\\n\\nOutput your evaluation as a JSON obje [...] the JSON dict, lay out your reasoning step by step.\\n\nReference: {\"coherence\": 4.7, \"consistency\": 5.0, \"fluency\": 5.0, \"relevance\": 5.0}\nActual: ['To evaluate the quality of the given summary, I will assess it on four dimensions: coherence, consistency, fluency, and relevance. Here\\'s [...] w if you\\'d like me to clarify any of my reasoning!']", "timestamp": "2024-08-20T08:20:32.700167Z", "severity": "INFO", "labels": {"view": "query-processing", "searchId": ""}}
{"message": "Evaluated 301/2100 queries.", "timestamp": "2024-08-20T08:20:32.

{"message": "Cache miss for key: {\"base_url\": \"https://api.deepinfra.com/v1/openai/\", \"max_tokens\": 4096, \"messages\": [{\"content\": \"Y..., fetching from API.", "timestamp": "2024-08-20T08:20:40.653843Z", "severity": "INFO", "labels": {"view": "query-processing", "searchId": ""}}
{"message": "Cache miss for key: {\"base_url\": \"https://api.deepinfra.com/v1/openai/\", \"max_tokens\": 4096, \"messages\": [{\"content\": \"Y..., fetching from API.", "timestamp": "2024-08-20T08:20:40.665164Z", "severity": "INFO", "labels": {"view": "query-processing", "searchId": ""}}
{"message": "Cache miss for key: {\"base_url\": \"https://api.deepinfra.com/v1/openai/\", \"max_tokens\": 4096, \"messages\": [{\"content\": \"Y..., fetching from API.", "timestamp": "2024-08-20T08:20:40.670947Z", "severity": "INFO", "labels": {"view": "query-processing", "searchId": ""}}
{"message": "Cache hit from key: {\"base_url\": \"https://api.deepinfra.com/v1/openai/\", \"max_tokens\": 4096, \"messages\": [{\"

[Prompt(prompt='\nYou will evaluate the quality of a given summary, with respect to a  [...] asoning step by step.\n' (len=393), mean_score=0.4482, mean_validation_score=0.4819, zero_score_cases=False),
 Prompt(prompt='Your task is to assess the effectiveness of a summary in relation to a [...] cified range of 1 to 5.' (len=757), mean_score=0.4256, mean_validation_score=0.4686, zero_score_cases=False),
 Prompt(prompt='Assess the quality of a provided summary in relation to a reference te [...] d on a scale of 1 to 5.' (len=588), mean_score=0.3926, mean_validation_score=0.5055, zero_score_cases=False),
 Prompt(prompt='Assess the quality of a provided summary in relation to a given refere [...] ecedes the JSON output.' (len=612), mean_score=0.4360, mean_validation_score=0.4348, zero_score_cases=False),
 Prompt(prompt='Assess the summary provided by evaluating its alignment with the refer [...] ation to the reference.' (len=680), mean_score=0.3287, mean_validation_score=0.4465, zero_score

In [16]:
cum_perf_incr = [
    max(prompt_set_se[: i + 1], key=lambda x: x.mean_validation_score)
    for i in range(len(prompt_set_se))
]
cum_perf_incr

[Prompt(prompt='\nYou will evaluate the quality of a given summary, with respect to a  [...] asoning step by step.\n' (len=393), mean_score=0.4482, mean_validation_score=0.4819, zero_score_cases=False),
 Prompt(prompt='\nYou will evaluate the quality of a given summary, with respect to a  [...] asoning step by step.\n' (len=393), mean_score=0.4482, mean_validation_score=0.4819, zero_score_cases=False),
 Prompt(prompt='Assess the quality of a provided summary in relation to a reference te [...] d on a scale of 1 to 5.' (len=588), mean_score=0.3926, mean_validation_score=0.5055, zero_score_cases=False),
 Prompt(prompt='Assess the quality of a provided summary in relation to a reference te [...] d on a scale of 1 to 5.' (len=588), mean_score=0.3926, mean_validation_score=0.5055, zero_score_cases=False),
 Prompt(prompt='Assess the quality of a provided summary in relation to a reference te [...] d on a scale of 1 to 5.' (len=588), mean_score=0.3926, mean_validation_score=0.5055, zero_score

In [17]:
from matplotlib import pyplot as plt

fig, ax = plt.subplots(figsize=(6, 3))

ax.plot([p.mean_validation_score for p in cum_perf_incr], color="blue")

# despine
ax.spines["top"].set_visible(False)
ax.spines["right"].set_visible(False)

# grid
ax.yaxis.grid(color="gray", linestyle="dashed")
ax.xaxis.grid(color="gray", linestyle="dashed")

# labels
ax.set_xlabel("Optimisation step")
ax.set_ylabel("Best performance")

Text(0, 0.5, 'Best performance')